In [36]:
import pandas as pd
import numpy as np
from sklearn import preprocessing, metrics
from sklearn.metrics.pairwise import linear_kernel, cosine_similarity, paired_euclidean_distances
from sklearn.manifold import TSNE
from sklearn.cluster import KMeans
import plotly.graph_objects as go
from plotly.graph_objs import *

df = pd.read_csv('metrics.csv')
print(df.shape)
df.head()

(22481, 19)


file             author  \
0     project_gutenberg/9999.txt  Sarah H. Bradford   
1  project_gutenberg/56195-0.txt       Kenneth Ward   
2    project_gutenberg/51187.txt        John Wilson   
3    project_gutenberg/51185.txt  Daniel F. Galouye   
4     project_gutenberg/9997.txt    Francis Parkman   

                                             title  year      sttr  \
0                 Harriet, The Moses of Her People  1822  0.624214   
1          The Boy Volunteers on the Belgian Front  1941  0.585125   
2          A Visit to the Mammoth Cave of Kentucky  1972  0.620000   
3                           All Jackson's Children  1970  0.627000   
4  France and England in North America, Part Third  2013  0.686821   

   hapax_legomenon      yules_k  function_words  avg_sentence_length_word  \
0         0.452214   528.796852        0.398840                 20.889773   
1         0.415000   378.878385        0.397120                 14.213115   
2         0.444000  1298.919399        0.428477                 27.300300   
3         0.486000  1703.701946        0.324357                  8.565289   
4         0.541750   269.095482        0.372508                 21.562230   

   avg_sentence_length_chars  avg_syllables_per_word  punctuation_sentence  \
0                 111.791794                1.735272              4.017759   
1                  77.207650                1.752356              2.763206   
2                 146.405405                1.720949              4.384384   
3                  49.239669                1.794130              2.674380   
4                 122.567266                1.868661              4.204856   

   shannon_entropy  simpsons_d  average_nps  noun_to_verb  noun_to_adj  \
0        10.845536    0.998584   232.700000      0.640382     0.792910   
1        10.506952    0.997945   232.130435      0.603311     0.811363   
2        10.003001    0.998360   222.800000      0.656081     0.777569   
3         9.511655    0.996898   221.166667      0.586852     0.823569   
4        11.781284    0.998751   241.057143      0.716877     0.837261   

   verb_to_adv  avg_dependency_distance  
0     0.717273                 2.338342  
1     0.718462                 2.134627  
2     0.638938                 2.403897  
3     0.692679                 2.098842  
4     0.751203                 2.331626

## Recommendation System

In [2]:
## standard scaling all style metrics; each will have mean 0 and std 1
metrics = df.iloc[:, 4:].values
scaler = preprocessing.MinMaxScaler()
metrics_scaled = scaler.fit_transform(metrics)
df_scaled = pd.DataFrame(metrics_scaled, columns=df.columns[4:])
df_scaled = pd.concat([df.iloc[:,:4], df_scaled], axis=1)
df_scaled.head()

file             author  \
0     project_gutenberg/9999.txt  Sarah H. Bradford   
1  project_gutenberg/56195-0.txt       Kenneth Ward   
2    project_gutenberg/51187.txt        John Wilson   
3    project_gutenberg/51185.txt  Daniel F. Galouye   
4     project_gutenberg/9997.txt    Francis Parkman   

                                             title  year      sttr  \
0                 Harriet, The Moses of Her People  1822  0.582054   
1          The Boy Volunteers on the Belgian Front  1941  0.538170   
2          A Visit to the Mammoth Cave of Kentucky  1972  0.577322   
3                           All Jackson's Children  1970  0.585181   
4  France and England in North America, Part Third  2013  0.652340   

   hapax_legomenon   yules_k  function_words  avg_sentence_length_word  \
0         0.424011  0.050913        0.770105                  0.255357   
1         0.384411  0.035721        0.766781                  0.164938   
2         0.415270  0.128954        0.827354                  0.342173   
3         0.459963  0.169973        0.626222                  0.088452   
4         0.519287  0.024596        0.719238                  0.264464   

   avg_sentence_length_chars  avg_syllables_per_word  punctuation_sentence  \
0                   0.229973                0.450676              0.073988   
1                   0.150698                0.461159              0.050793   
2                   0.309316                0.441888              0.080766   
3                   0.086589                0.486792              0.049151   
4                   0.254673                0.532525              0.077447   

   shannon_entropy  simpsons_d  average_nps  noun_to_verb  noun_to_adj  \
0         0.704748    0.996935     0.670464      0.404288     0.517212   
1         0.669873    0.995548     0.668741      0.342800     0.560263   
2         0.617966    0.996449     0.640524      0.430328     0.481421   
3         0.567358    0.993278     0.635585      0.315501     0.588741   
4         0.801130    0.997296     0.695737      0.531166     0.620684   

   verb_to_adv  avg_dependency_distance  
0     0.502914                 0.323430  
1     0.505006                 0.247857  
2     0.365188                 0.347749  
3     0.459674                 0.234581  
4     0.562570                 0.320938

In [ ]:
[['sttr', 'hapax_legomenon', 'yules_k', 'function_words', 
  'avg_sentence_length_word', 'avg_sentence_length_chars', 
  'avg_syllables_per_word', 'punctuation_sentence', 
  'shannon_entropy', 'simpsons_d', 'average_nps', 'noun_to_verb', 
  'noun_to_adj', 'verb_to_adv', 'avg_dependency_distance']]

In [3]:
df_scaled_subset = df_scaled[['sttr', 'hapax_legomenon', 'yules_k',
                              'avg_sentence_length_word', 'avg_sentence_length_chars', 
                              'avg_syllables_per_word', 'punctuation_sentence', 'shannon_entropy', 
                              'simpsons_d', 'average_nps', 'noun_to_verb', 'noun_to_adj', 
                              'verb_to_adv','avg_dependency_distance'
                              ]]

In [4]:
## scaled cosine sim
cosine_sim = cosine_similarity(df_scaled_subset, df_scaled_subset)

In [5]:
indices = pd.Series(df.index, index=df['title'])

In [103]:
# takes book title as input and outputs most similar books
def get_recommendations(title, cosine_sim=cosine_sim):
    # gets index of book that matches title
    idx = indices[title]

    # gets pairwise similarity scores of all books with that book
    sim_scores = list(enumerate(cosine_sim[idx]))

    # sorts books based on the similarity scores
    sim_scores = sorted(sim_scores, key=lambda x: x[1], reverse=True)

    # gets scores of the 10 most similar movies
    sim_scores = sim_scores[1:11]

    # gets book indices
    book_indices = [i[0] for i in sim_scores]

    # returns top 10 most similar books
    return df[['author', 'title']].iloc[book_indices], df[df['title'] == title]

In [105]:
recs, input_ = get_recommendations('The Logic of Hegel')

In [110]:
input_

file          author               title  year  \
1647  project_gutenberg/55108-0.txt  G. W. F. Hegel  The Logic of Hegel  1770   

          sttr  hapax_legomenon     yules_k  function_words  \
1647  0.579323         0.416516  159.650794        0.431336   

      avg_sentence_length_word  avg_sentence_length_chars  \
1647                 20.615007                 120.761814   

      avg_syllables_per_word  punctuation_sentence  shannon_entropy  \
1647                 2.30144              3.710745        11.185264   

      simpsons_d  average_nps  noun_to_verb  noun_to_adj  verb_to_adv  \
1647    0.998725    226.19774      0.718977     0.732031     0.613337   

      avg_dependency_distance  
1647                 2.319899

In [109]:
recs

author  \
11307  Georg Wilhelm Friedrich Hegel   
4893                 August Weismann   
15548               Frederick Engels   
13338           William E. Kellicott   
16955                  Ernst Haeckel   
7096               Norman Kemp Smith   
17371             William Platt Ball   
12940               Friedrich Engels   
19754              St. George Mivart   
17661         A.C. Seward and Others   

                                                   title  
11307                         Hegel’s Philosophy of Mind  
4893   Studies in the Theory of Descent, Volume II (o...  
15548  The Origin of the Family Private Property and ...  
13338                  The Social Direction of Evolution  
16955                        Evolution in Modern Thought  
7096    A Commentary to Kant's 'Critique of Pure Reason'  
17371       Are the Effects of Use and Disuse Inherited?  
12940                  Landmarks of Scientific Socialism  
19754                          On the Genesis of Species  
17661                          Darwin and Modern Science

## Clustering

In [111]:
X = df_scaled_subset

In [45]:
## elbow method
distorsions = []

# Calculate SSE for different k
for k in range(2, 30):
    kmeans = KMeans(n_clusters=k, random_state = 301)
    kmeans.fit(X)
    distorsions.append(kmeans.inertia_)

In [46]:
f = go.Figure()
f.add_trace(go.Scatter(x=list(range(2, 30)), 
                       y=distorsions, 
                       line_color='rgb(0, 200, 200)', 
                       showlegend=False,
                       name='Elbow curve'
                      ))

f.update_layout(title='Elbow curve',
                height=600,
                width=500)

f.update_xaxes(title='k',
               nticks=29)

f.update_yaxes(title='WSS')

f.show()

In [42]:
## silhouette score 
silhouette_plot = []
for k in range(2, 30):
    clusters = KMeans(n_clusters=k, random_state=10)
    cluster_labels = clusters.fit_predict(X)
    silhouette_avg = metrics.silhouette_score(X, cluster_labels)
    silhouette_plot.append(silhouette_avg)

In [43]:
f = go.Figure()
f.add_trace(go.Scatter(x=list(range(2, 30)), 
                       y=silhouette_plot, 
                       line_color='rgb(0, 0, 100)', 
                       showlegend=False,
                       name='Silhouette coefficients over k'
                      ))

f.update_layout(title='Silhouette coefficients over k',
                height=600,
                width=500)

f.update_xaxes(title='k',
               nticks=29)

f.update_yaxes(title='silhouette coefficient')

f.show()

In [62]:
## performing k-means clustering
k_means = KMeans(n_clusters=7)
k_means.fit(X)
clusters = k_means.predict(X)

In [92]:
## TSNE for dimensionality reduction
metrics_embedded = TSNE(n_components=3).fit_transform(df_scaled_subset)

df_TSNE = pd.concat([df.iloc[:, :4], 
                     pd.DataFrame(metrics_embedded, columns=['TSNE_1', 
                                                             'TSNE_2', 
                                                             'TSNE_3'])], axis=1)

In [96]:
## visualizing clusters
f = go.Figure(data=go.Scatter3d(x=df_TSNE.TSNE_1, 
                                y=df_TSNE.TSNE_2,
                                z=df_TSNE.TSNE_3,
                                mode='markers',
                                marker=dict(size=2,
                                            color=clusters, 
                                            colorscale='PRGn', 
                                            reversescale=True,
                                            opacity=.5),
                                text='<b>' + df_TSNE['title'] + '</b>'
                                     '<br>' + 
                                      df_TSNE['author'] + ', ' +
                                      df['year'].astype('str'),
                                hovertemplate='%{text} <extra></extra>',
                                hoverlabel=dict(bgcolor='black',
                                                align='left')
                               ))

f.update_layout(title='Stylometric Analysis of Project Gutenberg',
                height=1100,
                width=1100,
                template='plotly_white')
f.show()